# Recommender Systems Tutorial
In this tutorial, we'll provide a simple walkthrough of how to use Snorkel to to improve recommendations.
We will use the [Goodreads](https://sites.google.com/eng.ucsd.edu/ucsdbookgraph/home) dataset, from
"Item Recommendation on Monotonic Behavior Chains", RecSys'18 (Mengting Wan, Julian McAuley), and "Fine-Grained Spoiler Detection from Large-Scale Review Corpora", ACL'19, Mengting Wan, Rishabh Misra, Ndapa Nakashole, Julian McAuley. In this dataset, we have user ratings and reviews for Young Adult novels from the Goodreads website, along with metadata (like authors) for the novels. We consider the task of predicting whether a user will read and like any given book.

In [1]:
import os

if os.path.basename(os.getcwd()) == "snorkel-tutorials":
    os.chdir("recsys")

## Loading Data

We run the `download_data` function to download and preprocess the data. The function returns the `df_books` dataframe, which contains one row per book, along with metadata for that book. It also contains the `data_train`, `data_test`, `data_val`, `data_val` dataframes, which correspond to our training, test, development, and validation sets. Each of those dataframes has the following fields:
* `user_idx`: A unique identifier for a user.
* `book_idx`: A unique identifier for a book that is being rated by the user.
* `book_idxs`: The set of books that the user has interacted with (read or planned to read).
* `review_text`: Optional text review written by the user for the book.
* `rating`: Either `0` (which means the user did not read or did not like the book) or `1` (which means the user read and liked the book). The `rating` field is missing for `data_train`.
Our objective is to predict whether a given user (represented by the set of book_idxs the user has interacted with) will read and like any given book. That is, we want to train a model that takes a set of `book_idxs` and a `book_idx` as input and predicts the `rating`.

In [2]:
from data import download_and_process_data

df_books, (data_train, data_test, data_dev, data_val) = download_and_process_data()

data_dev.head()

/home/ubuntu/snorkel-tutorials/recsys/data.py:167: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  df_interactions_nz["rating_4_5"] = df_interactions_nz.rating.map(ratings_map)


user_idx                                          book_idxs  book_idx  \
159        12  (26338, 29959, 1906, 30378, 25725, 7549, 21355...     26338   
160        12  (26338, 29959, 1906, 30378, 25725, 7549, 21355...     29959   
161        12  (26338, 29959, 1906, 30378, 25725, 7549, 21355...      1906   
162        12  (26338, 29959, 1906, 30378, 25725, 7549, 21355...     25725   
163        12  (26338, 29959, 1906, 30378, 25725, 7549, 21355...     21355   

     rating review_text  
159       0         NaN  
160       1         NaN  
161       0         NaN  
162       1         NaN  
163       1         NaN

If a user has interacted with several books written by an author, there is a good chance that the user will read and like other books by the same author. We express this as a labeling function, using the `first_author` field in the `df_books` dataframe.

In [3]:
from snorkel.labeling.lf import labeling_function

book_to_first_author = dict(zip(df_books.book_idx, df_books.first_author))
first_author_to_books_df = df_books.groupby("first_author")[["book_idx"]].agg(set)
first_author_to_books = dict(
    zip(first_author_to_books_df.index, first_author_to_books_df.book_idx)
)


@labeling_function()
def common_first_author(x):
    author = book_to_first_author[x.book_idx]
    same_author_books = first_author_to_books[author]
    num_read = len(set(x.book_idxs).intersection(same_author_books))
    return 1 if num_read > 8 else -1

We can also leverage the long text reviews written by users to guess whether they liked or disliked a book. We run [TextBlob](https://textblob.readthedocs.io/en/dev/index.html), a tool that provides a pretrained sentiment analyzer, on the reviews, and use its polarity and subjectivity scores to estimate the user's rating for the book.

In [4]:
from snorkel.preprocess import preprocessor
from textblob import TextBlob


@preprocessor()
def textblob_polarity(x):
    if x.review_text:
        x.blob = TextBlob(str(x.review_text))
        x.start_blob = TextBlob(" ".join(x.blob.raw_sentences[:2]))
    else:
        x.blob = None
    return x


textblob_polarity.memoize = True

# Label high polarity reviews as positive.
@labeling_function(pre=[textblob_polarity])
def polarity_positive(x):
    if x.blob:
        if x.blob.polarity > 0.3:
            return 1
    return -1


# Label high subjectivity reviews as positive.
@labeling_function(pre=[textblob_polarity])
def subjectivity_positive(x):
    if x.blob:
        if x.blob.subjectivity > 0.75:
            return 1
    return -1


# Label low polarity reviews as negative.
@labeling_function(pre=[textblob_polarity])
def polarity_negative(x):
    if x.blob:
        if x.blob.polarity < 0.0:
            return 0
    return -1

In [5]:
from snorkel.labeling import PandasLFApplier, LFAnalysis

lfs = [common_first_author, polarity_positive, subjectivity_positive, polarity_negative]

applier = PandasLFApplier(lfs)
L_dev = applier.apply(data_dev)
LFAnalysis(L_dev, lfs).lf_summary(data_dev.rating)

  0%|          | 0/82999 [00:00<?, ?it/s]

  0%|          | 34/82999 [00:00<04:07, 334.90it/s]

  0%|          | 84/82999 [00:00<03:43, 370.70it/s]

  0%|          | 147/82999 [00:00<03:16, 421.79it/s]

  0%|          | 208/82999 [00:00<02:58, 463.51it/s]

...

100%|█████████▉| 82791/82999 [02:25<00:00, 658.46it/s]

100%|█████████▉| 82859/82999 [02:25<00:00, 557.55it/s]

100%|█████████▉| 82933/82999 [02:25<00:00, 600.56it/s]

100%|██████████| 82999/82999 [02:25<00:00, 569.36it/s]

j Polarity  Coverage  Overlaps  Conflicts  Correct  \
common_first_author    0      [1]  0.105001  0.003024   0.000554     5798   
polarity_positive      1      [1]  0.050543  0.013012   0.000000     3393   
subjectivity_positive  2      [1]  0.019542  0.014325   0.002735     1221   
polarity_negative      3      [0]  0.017482  0.003169   0.003169      830   

                       Incorrect  Emp. Acc.  
common_first_author         2917   0.665290  
polarity_positive            802   0.808820  
subjectivity_positive        401   0.752774  
polarity_negative            621   0.572019

### Applying labeling functions to the training set

We apply the labeling functions to the training set, and then filter out examples unlabeled by any LF, and combine the rest with the dev set to form our final training set.

In [6]:
from snorkel.labeling.model.label_model import LabelModel

# Train LabelModel.
L_train = applier.apply(data_train)
label_model = LabelModel(cardinality=2, verbose=True)
label_model.fit(L_train, n_epochs=5000, seed=123, log_freq=20, lr=0.01)

from snorkel.analysis import metric_score
from snorkel.utils import probs_to_preds

Y_dev_prob = label_model.predict_proba(L_dev)
Y_dev_pred = probs_to_preds(Y_dev_prob)

acc = metric_score(data_dev.rating, Y_dev_pred, probs=None, metric="accuracy")
print(f"LabelModel Accuracy: {acc:.3f}")

Y_train_prob = label_model.predict_proba(L_train)
Y_train_preds = probs_to_preds(Y_train_prob)

  0%|          | 0/602399 [00:00<?, ?it/s]

  0%|          | 7/602399 [00:00<2:23:30, 69.96it/s]

  0%|          | 76/602399 [00:00<1:44:49, 95.76it/s]

  0%|          | 148/602399 [00:00<1:17:33, 129.41it/s]

  0%|          | 216/602399 [00:00<58:47, 170.71it/s]  

...

100%|█████████▉| 602206/602399 [17:03<00:00, 387.45it/s]

100%|█████████▉| 602275/602399 [17:03<00:00, 445.80it/s]

100%|█████████▉| 602349/602399 [17:03<00:00, 505.54it/s]

100%|██████████| 602399/602399 [17:03<00:00, 588.37it/s]

LabelModel Accuracy: 0.499


In [7]:
import pandas as pd
from snorkel.labeling import filter_unlabeled_dataframe

data_train_filtered, Y_train_prob_filtered = filter_unlabeled_dataframe(
    data_train, Y_train_prob, L_train
)
Y_train_preds_filtered = probs_to_preds(Y_train_prob_filtered)
data_train_filtered["rating"] = Y_train_preds_filtered
combined_data_train = pd.concat([data_train_filtered, data_dev], axis=0)

/home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/ipykernel_launcher.py:9: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  if __name__ == '__main__':


### Rating Prediction Model
We write a Keras model for predicting ratings given a user's book list and a book (which is being rated). The model represents the list of books the user interacted with, `books_idxs`, by learning an embedding for each idx, and averaging the embeddings in `book_idxs`. It learns another embedding for the `book_idx`, the book to be rated. Then it concatenates the two embeddings and uses an [MLP](https://en.wikipedia.org/wiki/Multilayer_perceptron) to compute the probability of the `rating` being 1.

In [8]:
import numpy as np
import tensorflow as tf
from tensorflow.keras import backend as K

early_stopping = tf.keras.callbacks.EarlyStopping(
    monitor="val_acc", patience=10, verbose=1, restore_best_weights=True
)
n_books = len(df_books)


def recall_m(y_true, y_pred):
    true_positives = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
    possible_positives = K.sum(K.round(K.clip(y_true, 0, 1)))
    recall = true_positives / (possible_positives + K.epsilon())
    return recall


def precision_m(y_true, y_pred):
    true_positives = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
    predicted_positives = K.sum(K.round(K.clip(y_pred, 0, 1)))
    precision = true_positives / (predicted_positives + K.epsilon())
    return precision


def f1_m(y_true, y_pred):
    precision = precision_m(y_true, y_pred)
    recall = recall_m(y_true, y_pred)
    return 2 * ((precision * recall) / (precision + recall + K.epsilon()))


def get_feedforward_model():
    num_b = tf.keras.layers.Input([], name="inp_num_b")
    bids = tf.keras.layers.Input([None], name="inp_bids")
    bid = tf.keras.layers.Input([], name="inp_bid")
    bi_emb_dim = 64
    b_emb_dim = 64
    layer_sizes = [32]
    bi_emb = tf.keras.layers.Embedding(n_books, bi_emb_dim, name="bi_emb")(bids)
    b_emb = tf.keras.layers.Embedding(n_books, b_emb_dim, name="b_emb")(bid)
    bi_emb_reduced = tf.math.divide(
        tf.keras.backend.sum(bi_emb, axis=1),
        tf.expand_dims(num_b, 1),
        name="bi_emb_reduced",
    )
    input_layer = tf.keras.layers.concatenate(
        [bi_emb_reduced, b_emb], 1, name="input_layer"
    )
    cur_layer = input_layer
    for size in layer_sizes:
        tf.keras.layers.Dense(size, activation=tf.nn.relu)(cur_layer)
    output_layer = tf.keras.layers.Dense(1, activation=tf.nn.sigmoid)(cur_layer)
    feedforward_model = tf.keras.Model(
        inputs=[num_b, bids, bid], outputs=[output_layer]
    )
    feedforward_model.compile(
        "Adagrad",
        "binary_crossentropy",
        metrics=["accuracy", f1_m, precision_m, recall_m],
    )
    return feedforward_model


padded_shapes = {"num_b": [], "bids": [None], "bid": [], "label": []}


def get_data_tensors(data):
    def generator():
        for bids, bid, rating in zip(data.book_idxs, data.book_idx, data.rating):
            if len(bids) <= 1:
                continue
            yield {"num_b": len(bids), "bids": bids, "bid": bid, "label": rating}
            if rating == 1:
                yield {
                    "num_b": len(bids),
                    "bids": bids,
                    "bid": np.random.randint(0, n_books),
                    "label": 0,
                }

    dataset = (
        tf.data.Dataset.from_generator(generator, {k: tf.int64 for k in padded_shapes})
        .shuffle(123)
        .repeat(None)
        .padded_batch(256, padded_shapes, drop_remainder=False)
    )
    tensor_dict = tf.compat.v1.data.make_one_shot_iterator(dataset).get_next()
    return (
        tensor_dict["num_b"],
        tensor_dict["bids"],
        tensor_dict["bid"],
        tensor_dict["label"],
    )

/home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/ubuntu/snorkel-t

/home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorboard/compat/tensorflow_stub/dtypes.py:541: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorboard/compat/tensorflow_stub/dtypes.py:542: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorboard/compat/tensorflow_stub/dtypes.py:543: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/

In [9]:
feedforward_model = get_feedforward_model()

train_data_tensors = get_data_tensors(combined_data_train)
val_data_tensors = get_data_tensors(data_val)
feedforward_model.fit(
    train_data_tensors[:-1],
    train_data_tensors[-1],
    steps_per_epoch=300,
    validation_data=(val_data_tensors[:-1], val_data_tensors[-1]),
    validation_steps=40,
    # callbacks=[early_stopping],
    epochs=50,
    verbose=1,
)

W0809 05:56:43.356692 140506553599808 deprecation.py:506] From /home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorflow/python/keras/initializers.py:119: calling RandomUniform.__init__ (from tensorflow.python.ops.init_ops) with dtype is deprecated and will be removed in a future version.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor


W0809 05:56:43.443808 140506553599808 deprecation.py:506] From /home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorflow/python/ops/init_ops.py:1251: calling VarianceScaling.__init__ (from tensorflow.python.ops.init_ops) with dtype is deprecated and will be removed in a future version.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor


W0809 05:56:43.580631 140506553599808 deprecation.py:323] From /home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorflow/python/ops/nn_impl.py:180: add_dispatch_support.<locals>.wrapper (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


W0809 05:56:43.603703 140506553599808 deprecation.py:323] From /home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorflow/python/data/ops/dataset_ops.py:494: py_func (from tensorflow.python.ops.script_ops) is deprecated and will be removed in a future version.
Instructions for updating:
tf.py_func is deprecated in TF V2. Instead, there are two
    options available in V2.
    - tf.py_function takes a python function which manipulates tf eager
    tensors instead of numpy arrays. It's easy to convert a tf eager tensor to
    an ndarray (just call tensor.numpy()) but having access to eager tensors
    means `tf.py_function`s can use accelerators such as GPUs as well as
    being differentiable using a gradient tape.
    - tf.numpy_function maintains the semantics of the deprecated tf.py_func
    (it is not differentiable, and manipulates numpy arrays). It drops the
    stateful argument making all functions stateful.
    


W0809 05:56:43.797670 140506553599808 deprecation.py:506] From /home/ubuntu/snorkel-tutorials/.tox/recsys/lib/python3.6/site-packages/tensorflow/python/keras/optimizer_v2/adagrad.py:105: calling Constant.__init__ (from tensorflow.python.ops.init_ops) with dtype is deprecated and will be removed in a future version.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor


...

293/300 [============================>.] - ETA: 0s - loss: 0.5672 - acc: 0.7123 - f1_m: 0.3887 - precision_m: 0.7735 - recall_m: 0.2652

295/300 [============================>.] - ETA: 0s - loss: 0.5676 - acc: 0.7119 - f1_m: 0.3884 - precision_m: 0.7729 - recall_m: 0.2650

297/300 [============================>.] - ETA: 0s - loss: 0.5682 - acc: 0.7114 - f1_m: 0.3878 - precision_m: 0.7736 - recall_m: 0.2645

299/300 [============================>.] - ETA: 0s - loss: 0.5686 - acc: 0.7111 - f1_m: 0.3882 - precision_m: 0.7734 - recall_m: 0.2648

300/300 [==============================] - 12s 39ms/step - loss: 0.5687 - acc: 0.7109 - f1_m: 0.3878 - precision_m: 0.7727 - recall_m: 0.2644 - val_loss: 0.6575 - val_acc: 0.6490 - val_f1_m: 0.3478 - val_precision_m: 0.6331 - val_recall_m: 0.2470


In [10]:
test_data_tensors = get_data_tensors(data_test)
feedforward_model.evaluate(test_data_tensors[:-1], test_data_tensors[-1], steps=30)

 1/30 [>.............................] - ETA: 3s - loss: 0.6492 - acc: 0.6328 - f1_m: 0.3188 - precision_m: 0.6471 - recall_m: 0.2115

 3/30 [==>...........................] - ETA: 1s - loss: 0.6815 - acc: 0.6263 - f1_m: 0.2429 - precision_m: 0.6583 - recall_m: 0.1513

 5/30 [====>.........................] - ETA: 1s - loss: 0.6668 - acc: 0.6234 - f1_m: 0.2798 - precision_m: 0.6755 - recall_m: 0.1789

 7/30 [======>.......................] - ETA: 0s - loss: 0.6574 - acc: 0.6323 - f1_m: 0.3030 - precision_m: 0.6809 - recall_m: 0.1975

 9/30 [========>.....................] - ETA: 0s - loss: 0.6563 - acc: 0.6328 - f1_m: 0.3184 - precision_m: 0.6901 - recall_m: 0.2094

...

24/30 [=======================>......] - ETA: 0s - loss: 0.6554 - acc: 0.6411 - f1_m: 0.3268 - precision_m: 0.6731 - recall_m: 0.2223

26/30 [=========================>....] - ETA: 0s - loss: 0.6539 - acc: 0.6415 - f1_m: 0.3295 - precision_m: 0.6655 - recall_m: 0.2256

28/30 [===========================>..] - ETA: 0s - loss: 0.6542 - acc: 0.6417 - f1_m: 0.3273 - precision_m: 0.6505 - recall_m: 0.2258

30/30 [==============================] - 1s 30ms/step - loss: 0.6519 - acc: 0.6432 - f1_m: 0.3298 - precision_m: 0.6521 - recall_m: 0.2283


[0.6519375085830689, 0.6432292, 0.3297622, 0.65208954, 0.22826761]